# Expirence 2

# Introduction

## Differential Equations

\begin{equation}
\frac{di_1(t)}{dt}=D(t)\frac{v_1(t)}{L}-\frac{v_0(t)}{L}
\end{equation}

\begin{equation}
\frac{dv_0(t)}{dt}=D(t)\frac{i_1(t)}{C}-\frac{v_0(t)}{RC}
\end{equation}

### First equation in discreet format

\begin{equation}
\frac{i_1[t+step] - i_1[t]}{step}= D[t]\frac{v_1[t]}{L}-\frac{v_0[t]}{L}
\end{equation}
 
\begin{equation}
i_1[t+step]  = i_1[t] + step\cdot \left(D[t]\frac{v_1[t]}{L}-\frac{v_0[t]}{L}\right)
\end{equation}

### Second equation in discreet format
\begin{equation}
\frac{v_0[t+step] - v_0[t]}{step}=\frac{i_1(t)}{C}-\frac{v_0(t)}{RC}
\end{equation}
\begin{equation}
v_0[t+step] = v_0[t] + step\left(\frac{i_1(t)}{C}-\frac{v_0(t)}{RC}\right)
\end{equation}

## Differential Equations Discreet

\begin{equation}
i_1[t+step]  = i_1[t] + step\cdot \left(D[t]\frac{v_1[t]}{L}-\frac{v_0[t]}{L}\right)
\end{equation}

\begin{equation}
v_0[t+step] = v_0[t] + step\left(\frac{i_1(t)}{C}-\frac{v_0(t)}{RC}\right)
\end{equation} 

## 0.1 Dependencies

In [12]:
# Standard libraries: https://docs.python.org/3/library/
import math

# Analysis and plotting modules
import pandas as pd
import plotly


# cadCAD configuration modules
from cadCAD.configuration.utils import config_sim
from cadCAD.configuration import Experiment
from cadCAD import configs

# cadCAD simulation engine modules
from cadCAD.engine import ExecutionMode, ExecutionContext
from cadCAD.engine import Executor
import numpy as np

pd.options.plotting.backend = "plotly"

## 0.2 State Variables

In [5]:
initial_state = {
#    'i_o': 0, #A
    'i_1': 0, #A
    'v_o': 0, #V
#    'i_c': 0, #A
    'D': 0.5  #abs
}

initial_state

{'i_1': 0, 'v_o': 0, 'D': 0.5}

In [30]:
system_params = {
    'step': [0.000001],              #1μs
    'R': [1],                        #ohms
    'L': [math.pow(10,-3)],          #H
    'C': [800*math.pow(10,-6)],      #F
    'vi': [1],                       #V
    'fs': [5 * math.pow(10,3),
           1* math.pow(10,3),
           20 * math.pow(10,3)],     #5kHz
    'Rsh': [38.17],                  #ohms
    'Rs': [61.3*math.pow(10,-3)],    #ohms
    'beta': [86.14*math.pow(10,-3)], #V/K
    'n': [1.7536],                   #abs
    'Is': [5.68*math.pow(10,-6)],    #A
    'Iphn': [3.1656],                #A
    'Gn': [math.pow(10,3)],          #W/m2
    'T': [25]                        #°C
}


system_params

{'step': [1e-06],
 'R': [1],
 'L': [0.001],
 'C': [0.0007999999999999999],
 'vi': [1],
 'fs': [5000.0, 1000.0, 20000.0],
 'Rsh': [38.17],
 'Rs': [0.0613],
 'beta': [0.08614000000000001],
 'n': [1.7536],
 'Is': [5.68e-06],
 'Iphn': [3.1656],
 'Gn': [1000.0],
 'T': [25]}

## 0.3 Policy Functions

> A Policy Function computes one or more signals to be passed to State Update Functions. They describe the logic  and behaviour of a system component  or mechanism.

We'll cover this in the next section!

## 0.4 State Update Functions

In [31]:
def s_duty_cycle_a(params, substep, state_history, previous_state, policy_input):
    t = previous_state['timestep']*params['step']
    freq = params['fs']
    period = 1/freq
    dutycicle = 0.5
    if (t%period) < (period*dutycicle):
        pwm = 1
    else:
        pwm = 0
    return 'D', pwm


def s_i1(params, substep, state_history, previous_state, policy_input):
    L = params['L']
    vi = params['vi']
    step = params['step']
    i1 = previous_state['i_1'] + step*((previous_state['D'] * vi / L) - (previous_state['v_o']/L))
    return 'i_1', i1


def s_vo(params, substep, state_history, previous_state, policy_input):
    C = params['C']
    R = params['R']
    step = params['step']
    vo = previous_state['v_o'] + step*((previous_state['i_1']/C) - (previous_state['v_o']/(R*C)))
    return 'v_o', vo

# 5. Partial State Update Blocks
## Tying it all together

In [32]:
partial_state_update_blocks = [
    {
        'policies': {},
        'variables': {
            'D': s_duty_cycle_a,
            'i_1': s_i1,
            'v_o': s_vo
        }
    }
]

# 6. Configuration

In [33]:
sim_config = config_sim({
    "N": 1,
    "T": range(20000),
    "M": system_params
})

In [34]:
del configs[:] # Clear any prior configs
experiment = Experiment()
experiment.append_configs(
    initial_state = initial_state,
    partial_state_update_blocks = partial_state_update_blocks,
    sim_configs = sim_config
)
configs[-1].__dict__

{'sim_config': {'N': 3,
  'T': range(0, 20000),
  'M': {'step': 1e-06,
   'R': 1,
   'L': 0.001,
   'C': 0.0007999999999999999,
   'vi': 1,
   'fs': 20000.0,
   'Rsh': 38.17,
   'Rs': 0.0613,
   'beta': 0.08614000000000001,
   'n': 1.7536,
   'Is': 5.68e-06,
   'Iphn': 3.1656,
   'Gn': 1000.0,
   'T': 25},
  'subset_id': 2,
  'subset_window': deque([0, None]),
  'simulation_id': 0,
  'run_id': 2},
 'initial_state': {'i_1': 0, 'v_o': 0, 'D': 0.5},
 'seeds': {},
 'env_processes': {},
 'exogenous_states': {},
 'partial_state_updates': [{'policies': {},
   'variables': {'D': <function __main__.s_duty_cycle_a(params, substep, state_history, previous_state, policy_input)>,
    'i_1': <function __main__.s_i1(params, substep, state_history, previous_state, policy_input)>,
    'v_o': <function __main__.s_vo(params, substep, state_history, previous_state, policy_input)>}}],
 'policy_ops': [<function cadCAD.configuration.Experiment.<lambda>(a, b)>],
 'kwargs': {},
 'user_id': 'cadCAD_user',
 'ses

# 0.7 Execution

## Configuring the cadCAD simulation execution

In [35]:
exec_context = ExecutionContext()

In [36]:
simulation = Executor(exec_context=exec_context, configs=configs)

## Time to simulate our ecosystem model!

In [37]:
raw_result, tensor_field, sessions = simulation.execute()


                  ___________    ____
  ________ __ ___/ / ____/   |  / __ \
 / ___/ __` / __  / /   / /| | / / / /
/ /__/ /_/ / /_/ / /___/ ___ |/ /_/ /
\___/\__,_/\__,_/\____/_/  |_/_____/
by cadCAD

Execution Mode: local_proc
Configuration Count: 1
Dimensions of the first simulation: (Timesteps, Params, Runs, Vars) = (20000, 14, 3, 3)
Execution Method: local_simulations
SimIDs   : [0, 0, 0]
SubsetIDs: [0, 1, 2]
Ns       : [0, 1, 2]
ExpIDs   : [0, 0, 0]
Execution Mode: parallelized
Total execution time: 4.43s


# 0.8 Simulation Output Preparation

In [38]:
simulation_result = pd.DataFrame(raw_result)

In [39]:
simulation_result.head()

i_1           v_o    D  simulation  subset  run  substep  timestep
0  0.0000  0.000000e+00  0.5           0       0    1        0         0
1  0.0005  0.000000e+00  1.0           0       0    1        1         1
2  0.0015  6.250000e-07  1.0           0       0    1        1         2
3  0.0025  2.499219e-06  1.0           0       0    1        1         3
4  0.0035  5.621094e-06  1.0           0       0    1        1         4

# 0.9 Simulation Analysis

In [ ]:
simulation_result['subset'].replace

In [42]:
simulation_result.plot(kind='line', x='timestep', y='v_o', color='subset')

In [43]:
simulation_result.plot(kind='line', x='timestep', y='i_1', color='subset')